In [1]:
import pandas as pd
import folium
import numpy as np
import networkx as nx
from haversine import haversine

In [2]:
food = pd.read_csv('jeju_food.csv', encoding='cp949')
exfood = food.iloc[:10000]
exfood.columns

Index(['사업장명', '업종구분대분류', '업종구분소분류', '인허가일자', '인허가취소일자', '영업상태명', '상세영업상태명',
       '폐업일자', '휴업시작일자', '휴업종료일자', '재개업일자', '소재지면적', '소재지전체주소', '도로명전체주소',
       '도로명우편번호', '데이터갱신일자'],
      dtype='object')

In [21]:
data = pd.read_csv('jeju_market.csv')
df_rest = data[data['상권업종대분류명'] == '음식']
df_rest = df_rest[:2]
df_rest.head()

Unnamed: 0       상호명 상권업종대분류명 상권업종중분류명   상권업종소분류명  표준산업분류명      시도명 시군구명  \
0           2  아빠가닭튀기는집       음식     유흥주점      호프/맥주   기타 주점업  제주특별자치도  제주시   
1           5    숙성1퍼센트       음식       한식  한식/백반/한정식  한식 음식점업  제주특별자치도  제주시   

  행정동명 법정동명       행정동코드       법정동코드                        지번주소  \
0  한림읍  한림읍  5011025000  5011025024  제주특별자치도 제주시 한림읍 한림리 1199-3   
1  노형동  노형동  5011066000  5011012200      제주특별자치도 제주시 노형동 3785-3   

                   도로명주소    신우편번호   longitude   latitude  
0  제주특별자치도 제주시 한림읍 한림중앙로  63032.0  126.264860  33.412363  
1      제주특별자치도 제주시 노형10길  63083.0  126.479894  33.483335

In [32]:
def calDist(graph, curnode): #curnode는 노드 이름
    disDict = {}
    shortest_paths = nx.single_source_dijkstra_path_length(graph, curnode, weight='weight') ## cutoff는 curPos로부터최대 거리(이이상은 안찾음)
    print(f"Number of selected Node: {len(shortest_paths)}")
    for node, distance in shortest_paths.items():
        if node < 10000: ##node들은 4050000000이상임 음식점은 그것보다 작게 설정
            disDict[node] = distance 
    return disDict


In [23]:
nodes = pd.read_csv('Jeju_nodes.csv')
links = pd.read_csv('Jeju_links.csv')

nodes = nodes[['Id','NODE_NAME','latitude','longitude']]
links = links[['Source','Target','LENGTH']]
source_in = links['Source'].apply(lambda x : x in list(nodes['Id'])) # check Sources are in jeju_id
target_in = links['Target'].apply(lambda x : x in list(nodes['Id'])) # check Targets are in jeju_id
# source_in and target_in are boolean type pandas.Series which contains True or False
Jeju_links = links[source_in & target_in] # contain if both target and source are contained in jeju_id
G = nx.Graph()

for idx,row in nodes.iterrows():
    G.add_node(row['Id'],Label=row['NODE_NAME'],latitude=row['latitude'], longitude=row['longitude'])

for idx,row in Jeju_links.iterrows():    
    G.add_edge(row['Source'],row['Target'],weight = row['LENGTH'])

print(f"Nodes: {len(G.nodes)}, Edges: {len(G.edges)}")


Nodes: 4218, Edges: 6017


*ADDING LINK(너무 긴 링크의 경우 잘라서 노드를 추가하기)

In [6]:
# Maximum length for a single link (adjust as needed)
"""
max_length = 500  # 예시로 500으로 설정

new_nodes_data = []  # 새로 생성된 노드 데이터를 저장할 리스트
new_links_data = []  # 새로 생성된 링크 데이터를 저장할 리스트

for idx, row in Jeju_links.iterrows():
    source_node = row['Source']
    target_node = row['Target']
    length = row['LENGTH']

    if length > max_length:
        # Calculate the number of intermediate nodes required
        num_intermediate_nodes = int(length / max_length)

        # Calculate the coordinates of the intermediate nodes
        source_lat, source_lon = nodes[nodes['Id'] == source_node][['latitude', 'longitude']].values[0]
        target_lat, target_lon = nodes[nodes['Id'] == target_node][['latitude', 'longitude']].values[0]

        for i in range(1, num_intermediate_nodes + 1):
            fraction = i / (num_intermediate_nodes + 1)
            lat = source_lat + fraction * (target_lat - source_lat)
            lon = source_lon + fraction * (target_lon - source_lon)
            node_id = f"intermediate_{idx}_{i}"  # Unique node id for intermediate node

            new_nodes_data.append([node_id, f"Intermediate {i}", lat, lon])
            new_links_data.append([node_id, target_node, max_length])

            # Update target_node for the next iteration
            target_node = node_id

# Add intermediate nodes and links to the dataframes
new_nodes_df = pd.DataFrame(new_nodes_data, columns=['Id', 'NODE_NAME', 'latitude', 'longitude'])
new_links_df = pd.DataFrame(new_links_data, columns=['Source', 'Target', 'LENGTH'])

# Concatenate the new data with the existing data
nodes = pd.concat([nodes, new_nodes_df], ignore_index=True)
Jeju_links = pd.concat([Jeju_links, new_links_df], ignore_index=True)
"""

데이터에 새로 노드들 추가하기

In [24]:
def connectRes(graph, df): # df는 idx, latitude, longitude가 있어야함
    nodes_latitude = nx.get_node_attributes(graph, 'latitude')
    nodes_longitude = nx.get_node_attributes(graph, 'longitude')
    for idx, row in df.iterrows():
        distances ={}
        for keyLong, valLat in nodes_latitude.items():
            nodesPos = (valLat, nodes_longitude[keyLong])
            curPos = (row['latitude'], row['longitude'])
            distances[keyLong] = haversine(nodesPos, curPos, unit='km')
        nearest_node = min(distances, key=distances.get)
        graph.add_node(idx, Label=row['신우편번호'], latitude=row['latitude'], longitude=row['longitude']) ##노드이름은 4050000000이하로 설정
        graph.add_edge(nearest_node, idx, weight=distances[nearest_node]) 
    return graph

G = connectRes(G, df_rest)
print(f"Data: {len(df_rest)}, Nodes: {len(G.nodes)}, Edges: {len(G.edges)}")

Data: 2, Nodes: 4220, Edges: 6019


In [31]:
G[0]

AtlasView({4050134000: {'weight': 0.2430085827361106}})

In [33]:
print(calDist(G, 1))


Number of selected Node: 4218
{1: 0, 0: 24595.911856917235}


FOLIUM

In [34]:
std_point = tuple(nodes.head(4000)[['latitude','longitude']].iloc[3000]) # example of why we should add nodes

map_osm = folium.Map(location=std_point, zoom_start=15) 

# 도로망 표시
kw = {'opacity': 0.5, 'weight': 2}
for edge in G.edges(data=True):
    source, target, attributes = edge

    # Check if the source and target nodes exist in the graph
    if source in G.nodes and target in G.nodes:
        start = tuple([G.nodes[source]['latitude'], G.nodes[source]['longitude']])
        end = tuple([G.nodes[target]['latitude'], G.nodes[target]['longitude']])

        folium.PolyLine(
            locations=[start, end],
            color='blue',
            line_cap='round',
            **kw,
        ).add_to(map_osm)
    else:
        print(source, target)


# 식당 표시
for ix, row in df_rest.iterrows():
    location = (row['latitude'], row['longitude']) 
    folium.Circle(
        location=location,
        radius=500, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='red',
        fill=True,  
    ).add_to(map_osm)

# node 표시
for ix, row in nodes.iterrows():
    location = (row['latitude'], row['longitude']) 
    folium.Circle(
        location=location,
        radius=10, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='black',
        fill=True, 
    ).add_to(map_osm)


map_osm